In [12]:
import numpy as np
import pandas as pd
from numpy import array
import matplotlib.pyplot as plt

from sklearn.feature_selection import f_classif, mutual_info_classif, SelectFdr

from sklearn.feature_selection import GenericUnivariateSelect
from sklearn.svm import LinearSVC, NuSVC
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier 

from scipy.stats import uniform, randint

import numpy as np
import matplotlib.pyplot as plt
from sklearn.naive_bayes import GaussianNB
from sklearn.svm import SVC
from sklearn.datasets import load_digits
from sklearn.model_selection import learning_curve
from sklearn.model_selection import ShuffleSplit
from sklearn.model_selection import cross_val_score

import xgboost as xgb
from sklearn.metrics import auc, accuracy_score, confusion_matrix, mean_squared_error
from sklearn.model_selection import cross_val_score, GridSearchCV, KFold, RandomizedSearchCV, train_test_split

from warnings import filterwarnings
filterwarnings('ignore')


In [13]:

def plot_learning_curve(estimator, title, X, y, axes=None, ylim=None, cv=None,
                        n_jobs=None, train_sizes=np.linspace(.1, 1.0, 5)):
    """
    Generate 3 plots: the test and training learning curve, the training
    samples vs fit times curve, the fit times vs score curve.

    Parameters
    ----------
    estimator : object type that implements the "fit" and "predict" methods
        An object of that type which is cloned for each validation.

    title : string
        Title for the chart.

    X : array-like, shape (n_samples, n_features)
        Training vector, where n_samples is the number of samples and
        n_features is the number of features.

    y : array-like, shape (n_samples) or (n_samples, n_features), optional
        Target relative to X for classification or regression;
        None for unsupervised learning.

    axes : array of 3 axes, optional (default=None)
        Axes to use for plotting the curves.

    ylim : tuple, shape (ymin, ymax), optional
        Defines minimum and maximum yvalues plotted.

    cv : int, cross-validation generator or an iterable, optional
        Determines the cross-validation splitting strategy.
        Possible inputs for cv are:

          - None, to use the default 5-fold cross-validation,
          - integer, to specify the number of folds.
          - :term:`CV splitter`,
          - An iterable yielding (train, test) splits as arrays of indices.

        For integer/None inputs, if ``y`` is binary or multiclass,
        :class:`StratifiedKFold` used. If the estimator is not a classifier
        or if ``y`` is neither binary nor multiclass, :class:`KFold` is used.

        Refer :ref:`User Guide <cross_validation>` for the various
        cross-validators that can be used here.

    n_jobs : int or None, optional (default=None)
        Number of jobs to run in parallel.
        ``None`` means 1 unless in a :obj:`joblib.parallel_backend` context.
        ``-1`` means using all processors. See :term:`Glossary <n_jobs>`
        for more details.

    train_sizes : array-like, shape (n_ticks,), dtype float or int
        Relative or absolute numbers of training examples that will be used to
        generate the learning curve. If the dtype is float, it is regarded as a
        fraction of the maximum size of the training set (that is determined
        by the selected validation method), i.e. it has to be within (0, 1].
        Otherwise it is interpreted as absolute sizes of the training sets.
        Note that for classification the number of samples usually have to
        be big enough to contain at least one sample from each class.
        (default: np.linspace(0.1, 1.0, 5))
    """
    if axes is None:
        _, axes = plt.subplots(1, 3, figsize=(20, 5))

    axes[0].set_title(title)
    if ylim is not None:
        axes[0].set_ylim(*ylim)
    axes[0].set_xlabel("Training examples")
    axes[0].set_ylabel("Score")

    train_sizes, train_scores, test_scores, fit_times, _ = \
        learning_curve(estimator, X, y, cv=cv, n_jobs=n_jobs,
                       train_sizes=train_sizes,
                       return_times=True)
    train_scores_mean = np.mean(train_scores, axis=1)
    train_scores_std = np.std(train_scores, axis=1)
    test_scores_mean = np.mean(test_scores, axis=1)
    test_scores_std = np.std(test_scores, axis=1)
    fit_times_mean = np.mean(fit_times, axis=1)
    fit_times_std = np.std(fit_times, axis=1)

    # Plot learning curve
    axes[0].grid()
    axes[0].fill_between(train_sizes, train_scores_mean - train_scores_std,
                         train_scores_mean + train_scores_std, alpha=0.1,
                         color="r")
    axes[0].fill_between(train_sizes, test_scores_mean - test_scores_std,
                         test_scores_mean + test_scores_std, alpha=0.1,
                         color="g")
    axes[0].plot(train_sizes, train_scores_mean, 'o-', color="r",
                 label="Training score")
    axes[0].plot(train_sizes, test_scores_mean, 'o-', color="g",
                 label="Cross-validation score")
    axes[0].legend(loc="best")

    # Plot n_samples vs fit_times
    axes[1].grid()
    axes[1].plot(train_sizes, fit_times_mean, 'o-')
    axes[1].fill_between(train_sizes, fit_times_mean - fit_times_std,
                         fit_times_mean + fit_times_std, alpha=0.1)
    axes[1].set_xlabel("Training examples")
    axes[1].set_ylabel("fit_times")
    axes[1].set_title("Scalability of the model")

    # Plot fit_time vs score
    axes[2].grid()
    axes[2].plot(fit_times_mean, test_scores_mean, 'o-')
    axes[2].fill_between(fit_times_mean, test_scores_mean - test_scores_std,
                         test_scores_mean + test_scores_std, alpha=0.1)
    axes[2].set_xlabel("fit_times")
    axes[2].set_ylabel("Score")
    axes[2].set_title("Performance of the model")

    return plt

In [522]:
def hyper_opt_procedure(model_object,params,cv,perf_df,X,y):


  model = model_object()

  # Initial Model Fit with stock hyper_params

  init_score = np.mean(cross_val_score(model,X,y,cv=cv))

  perf_df = perf_df.append({'Model Iteration': 'Stock Params',
                              'Score':init_score}, ignore_index=True)

  print('Initial Model with Stock Params Score : {}'.format(init_score))

  # Random Search Cross Validation


  search_model = RandomizedSearchCV(model,
                                         param_distributions=params,
                                         random_state=42, 
                                         n_iter=300, 
                                         cv=cv, 
                                         verbose=1, 
                                         n_jobs=1, 
                                         return_train_score=True)

  search_model.fit(X,y)

  best_search_model = search_model.best_estimator_

  best_search_model_score = search_model.best_score_

  perf_df = perf_df.append({'Model Iteration': 'Random HP Search Best Model',
                      'Score':best_search_model_score}, ignore_index=True)

  rd_score_improv = ((best_search_model_score - init_score)/init_score) * 100

  print('Random HP Search Best Model Score : {}'.format(best_search_model_score))

  print('Improvement of {}% relative to the initial model'.format(rd_score_improv))
  
  


  return model, best_search_model
   



class hyper_model:
    
    def __init__(self,model_name,validation_approach,X,y):
        
        self.model_name = model_name
        self.X = X
        self.y = y
        self.validation_approach= validation_approach
        self.best_model = None
        self.best_params = None
        self.all_models_perf = pd.DataFrame(None,columns=['Model Iteration','Score'])
        self.stock_model = None
        self.rd_model = None


    def fit(self):


      if self.validation_approach == 'leave-one-run-out':

        cv = KFold(n_splits=8, shuffle=False)

      elif self.validation_approach == 'leave-one-run-out-shuffled':

        cv = KFold(n_splits=8, shuffle=True, random_state=42)

      elif self.validation_approach == 'leave-one-task-out':

        cv = KFold(n_splits=4, shuffle=False)

      elif self.validation_approach == 'leave-one-task-out-shuffled':

        cv = KFold(n_splits=4, shuffle=True, random_state=42)    


 
        
        # Linear SVM

      if self.model_name == 'linear_svm':

        params = {'C': [0.1, 1, 10]} 

        self.stock_model, self.rd_model = hyper_opt_procedure(model_object=LinearSVC,
                                                                                                 params=params,cv=cv,
                                                                                                 perf_df=self.all_models_perf,
                                                                                                 X=self.X,y=self.y)

         

      # Non Linear SVM


      elif self.model_name == 'non_linear_svm':

        params = { 'kernel': ['rbf','sigmoid']
                       }


        self.stock_model, self.rd_model = hyper_opt_procedure(model_object=NuSVC,
                                                                                                 params=params,cv=cv,
                                                                                                 perf_df=self.all_models_perf,
                                                                                                 X=self.X,y=self.y)

          
      # Random Forest Classifier


      elif self.model_name == 'random_forest_classifier':


        params = {'bootstrap': [True],
                    'max_depth': [60],
                    'max_features': ['auto'],
                    'min_samples_leaf': [4],
                    'min_samples_split': [2, 5],
                    'n_estimators': [1000]
                   }


        self.stock_model, self.rd_model = hyper_opt_procedure(model_object=RandomForestClassifier,
                                                                                                 params=params,cv=cv,
                                                                                                 perf_df=self.all_models_perf,
                                                                                                 X=self.X,y=self.y)
          



      # XG Boost Classifier


      elif self.model_name == 'xg_boost':

        params = {
              "gamma": [0.25,0.5]
              }

        self.stock_model, self.rd_model = hyper_opt_procedure(model_object=xgb.XGBClassifier,
                                                                                                 params=params,cv=cv,
                                                                                                 perf_df=self.all_models_perf,
                                                                                                 X=self.X,y=self.y)  

                
                

In [15]:
X = np.load('../../data/X_pref_lss_shift_constant_vmpfc.npy')

In [16]:
X.shape

(480, 419)

In [17]:
y = np.load('../../data/y_pref_lss_shift_constant_vmpfc.npy')

In [18]:
y.shape

(480, 1)

## Features Selection

### Filter

No FS needed, only 419 needeed

### Data Preparation

In [19]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.10, random_state=42)

## Linear Support Vector Machine

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [20]:
hm_linear_svm_to = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [21]:
hm_linear_svm_to.fit()

Initial Model with Stock Params Score : 0.5
Fitting 4 folds for each of 5 candidates, totalling 20 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    4.7s finished


Random HP Search Best Model Score : 0.5375
Improvement of 7.499999999999996% relative to the initial model


In [22]:
hm_linear_svm_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [23]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [24]:
scores

array([0.56666667, 0.41666667, 0.50833333, 0.44166667])

In [25]:
mean_score

0.48333333333333334

In [26]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [27]:
scores

array([0.21666667, 0.18333333, 0.16666667, 0.14166667])

In [28]:
mean_score

0.17708333333333331

In [29]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [30]:
scores

array([0.46666667, 0.58333333, 0.48333333, 0.55      , 0.55      ,
       0.48333333, 0.51666667, 0.45      ])

In [31]:
mean_score

0.5104166666666667

In [32]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [33]:
scores

array([0.11666667, 0.15      , 0.05      , 0.16666667, 0.1       ,
       0.08333333, 0.08333333, 0.08333333])

In [34]:
mean_score

0.10416666666666666

In [35]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [36]:
hm_linear_svm_tos = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [37]:
hm_linear_svm_tos.fit()

Initial Model with Stock Params Score : 0.1729166666666667
Fitting 4 folds for each of 5 candidates, totalling 20 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    4.0s finished


Random HP Search Best Model Score : 0.19999999999999998
Improvement of 15.662650602409615% relative to the initial model


In [38]:
hm_linear_svm_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [39]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [40]:
scores

array([0.46666667, 0.44166667, 0.5       , 0.5       ])

In [41]:
mean_score

0.4770833333333333

In [42]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [43]:
scores

array([0.2       , 0.19166667, 0.15      , 0.15      ])

In [44]:
mean_score

0.1729166666666667

In [45]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [46]:
scores

array([0.56666667, 0.56666667, 0.5       , 0.48333333, 0.5       ,
       0.46666667, 0.5       , 0.48333333])

In [47]:
mean_score

0.5083333333333333

In [48]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [49]:
scores

array([0.06666667, 0.13333333, 0.03333333, 0.15      , 0.13333333,
       0.08333333, 0.08333333, 0.11666667])

In [50]:
mean_score

0.1

In [51]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [52]:
hm_linear_svm_ro = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [53]:
hm_linear_svm_ro.fit()

Initial Model with Stock Params Score : 0.5041666666666667
Fitting 8 folds for each of 5 candidates, totalling 40 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:    8.9s finished


Random HP Search Best Model Score : 0.55
Improvement of 9.090909090909102% relative to the initial model


In [54]:
hm_linear_svm_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [55]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [56]:
scores

array([0.51666667, 0.45      , 0.51666667, 0.475     ])

In [57]:
mean_score

0.48958333333333337

In [58]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [59]:
scores

array([0.2       , 0.19166667, 0.15833333, 0.15      ])

In [60]:
mean_score

0.17500000000000002

In [61]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [62]:
scores

array([0.48333333, 0.55      , 0.43333333, 0.43333333, 0.48333333,
       0.48333333, 0.55      , 0.46666667])

In [63]:
mean_score

0.4854166666666667

In [64]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [65]:
scores

array([0.1       , 0.11666667, 0.05      , 0.16666667, 0.11666667,
       0.1       , 0.1       , 0.05      ])

In [66]:
mean_score

0.1

In [67]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [68]:
hm_linear_svm_ros = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [69]:
hm_linear_svm_ros.fit()

Initial Model with Stock Params Score : 0.10416666666666667
Fitting 8 folds for each of 5 candidates, totalling 40 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:    9.0s finished


Random HP Search Best Model Score : 0.13125
Improvement of 26.0% relative to the initial model


In [70]:
hm_linear_svm_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [71]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [72]:
scores

array([0.51666667, 0.45833333, 0.5       , 0.49166667])

In [73]:
mean_score

0.4916666666666667

In [74]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [75]:
scores

array([0.2       , 0.175     , 0.15      , 0.14166667])

In [76]:
mean_score

0.16666666666666669

In [77]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [78]:
scores

array([0.45      , 0.5       , 0.46666667, 0.5       , 0.46666667,
       0.48333333, 0.48333333, 0.55      ])

In [79]:
mean_score

0.4875

In [80]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [81]:
scores

array([0.1       , 0.13333333, 0.08333333, 0.15      , 0.11666667,
       0.08333333, 0.1       , 0.03333333])

In [82]:
mean_score

0.1

In [83]:
# other metrics + graphs




### Hyper_optimized model

#### *leave-one-task-out* cross validation

##### Training

In [84]:
hm_linear_svm_to = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [85]:
hm_linear_svm_to.fit()

Initial Model with Stock Params Score : 0.4854166666666667
Fitting 4 folds for each of 5 candidates, totalling 20 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    3.8s finished


Random HP Search Best Model Score : 0.5104166666666666
Improvement of 5.15021459227466% relative to the initial model


In [86]:
hm_linear_svm_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [87]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [88]:
scores

array([0.54166667, 0.48333333, 0.48333333, 0.45      ])

In [89]:
mean_score

0.4895833333333333

In [90]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [91]:
scores

array([0.21666667, 0.21666667, 0.2       , 0.18333333])

In [92]:
mean_score

0.20416666666666666

In [93]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [94]:
scores

array([0.48333333, 0.4       , 0.48333333, 0.55      , 0.46666667,
       0.5       , 0.46666667, 0.56666667])

In [95]:
mean_score

0.48958333333333337

In [96]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [97]:
scores

array([0.1       , 0.16666667, 0.06666667, 0.25      , 0.15      ,
       0.08333333, 0.15      , 0.11666667])

In [98]:
mean_score

0.13541666666666666

In [99]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [100]:
hm_linear_svm_tos = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [101]:
hm_linear_svm_tos.fit()

Initial Model with Stock Params Score : 0.17083333333333334
Fitting 4 folds for each of 5 candidates, totalling 20 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    3.5s finished


Random HP Search Best Model Score : 0.2041666666666667
Improvement of 19.51219512195123% relative to the initial model


In [102]:
hm_linear_svm_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [103]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [104]:
scores

array([0.50833333, 0.48333333, 0.53333333, 0.50833333])

In [105]:
mean_score

0.5083333333333333

In [106]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [107]:
scores

array([0.225     , 0.225     , 0.16666667, 0.18333333])

In [108]:
mean_score

0.2

In [109]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [110]:
scores

array([0.53333333, 0.48333333, 0.5       , 0.5       , 0.5       ,
       0.58333333, 0.5       , 0.46666667])

In [111]:
mean_score

0.5083333333333333

In [112]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [113]:
scores

array([0.13333333, 0.13333333, 0.05      , 0.16666667, 0.15      ,
       0.08333333, 0.15      , 0.1       ])

In [114]:
mean_score

0.12083333333333333

In [115]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [116]:
hm_linear_svm_ro = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [117]:
hm_linear_svm_ro.fit()

Initial Model with Stock Params Score : 0.5083333333333333
Fitting 8 folds for each of 5 candidates, totalling 40 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:    9.2s finished


Random HP Search Best Model Score : 0.5479166666666666
Improvement of 7.786885245901634% relative to the initial model


In [118]:
hm_linear_svm_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [119]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [120]:
scores

array([0.55833333, 0.36666667, 0.50833333, 0.23333333])

In [121]:
mean_score

0.4166666666666667

In [122]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [123]:
scores

array([0.16666667, 0.18333333, 0.15833333, 0.125     ])

In [124]:
mean_score

0.15833333333333333

In [125]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [126]:
scores

array([0.63333333, 0.48333333, 0.35      , 0.38333333, 0.5       ,
       0.51666667, 0.8       , 0.73333333])

In [127]:
mean_score

0.55

In [128]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [129]:
scores

array([0.08333333, 0.11666667, 0.05      , 0.11666667, 0.08333333,
       0.08333333, 0.06666667, 0.03333333])

In [130]:
mean_score

0.07916666666666666

In [131]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [132]:
hm_linear_svm_ros = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [133]:
hm_linear_svm_ros.fit()

Initial Model with Stock Params Score : 0.10208333333333333
Fitting 8 folds for each of 5 candidates, totalling 40 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:    9.1s finished


Random HP Search Best Model Score : 0.1375
Improvement of 34.69387755102042% relative to the initial model


In [134]:
hm_linear_svm_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [135]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [136]:
scores

array([0.50833333, 0.475     , 0.525     , 0.50833333])

In [137]:
mean_score

0.5041666666666667

In [138]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [139]:
scores

array([0.24166667, 0.23333333, 0.18333333, 0.19166667])

In [140]:
mean_score

0.2125

In [141]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [142]:
scores

array([0.48333333, 0.5       , 0.5       , 0.53333333, 0.53333333,
       0.51666667, 0.48333333, 0.5       ])

In [143]:
mean_score

0.50625

In [144]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [145]:
scores

array([0.13333333, 0.13333333, 0.13333333, 0.21666667, 0.13333333,
       0.1       , 0.15      , 0.1       ])

In [146]:
mean_score

0.1375

In [147]:
# other metrics + graphs




## Non Linear Support Vector Machine

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [148]:
hm_non_linear_svm_to = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [149]:
hm_non_linear_svm_to.fit()

Initial Model with Stock Params Score : 0.4395833333333333
Fitting 4 folds for each of 75 candidates, totalling 300 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5541666666666667
Improvement of 26.066350710900483% relative to the initial model


[Parallel(n_jobs=1)]: Done 300 out of 300 | elapsed:   17.4s finished


In [150]:
hm_non_linear_svm_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [151]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [152]:
scores

array([0.45      , 0.38333333, 0.475     , 0.45      ])

In [153]:
mean_score

0.4395833333333333

In [154]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [155]:
scores

array([0.43333333, 0.34166667, 0.29166667, 0.35833333])

In [156]:
mean_score

0.35625

In [157]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [158]:
scores

array([0.45      , 0.46666667, 0.31666667, 0.4       , 0.36666667,
       0.46666667, 0.56666667, 0.51666667])

In [159]:
mean_score

0.44375

In [160]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [161]:
scores

array([0.43333333, 0.35      , 0.33333333, 0.35      , 0.3       ,
       0.4       , 0.4       , 0.28333333])

In [162]:
mean_score

0.35625

In [163]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [164]:
hm_non_linear_svm_tos = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [165]:
hm_non_linear_svm_tos.fit()

Initial Model with Stock Params Score : 0.35625
Fitting 4 folds for each of 75 candidates, totalling 300 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.55
Improvement of 54.385964912280706% relative to the initial model


[Parallel(n_jobs=1)]: Done 300 out of 300 | elapsed:   17.6s finished


In [166]:
hm_non_linear_svm_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [167]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [168]:
scores

array([0.45      , 0.38333333, 0.475     , 0.45      ])

In [169]:
mean_score

0.4395833333333333

In [170]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [171]:
scores

array([0.43333333, 0.34166667, 0.29166667, 0.35833333])

In [172]:
mean_score

0.35625

In [173]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [174]:
scores

array([0.45      , 0.46666667, 0.31666667, 0.4       , 0.36666667,
       0.46666667, 0.56666667, 0.51666667])

In [175]:
mean_score

0.44375

In [176]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [177]:
scores

array([0.43333333, 0.35      , 0.33333333, 0.35      , 0.3       ,
       0.4       , 0.4       , 0.28333333])

In [178]:
mean_score

0.35625

In [179]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [180]:
hm_non_linear_svm_ro = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [181]:
hm_non_linear_svm_ro.fit()

Initial Model with Stock Params Score : 0.44375
Fitting 8 folds for each of 75 candidates, totalling 600 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.55
Improvement of 23.943661971831002% relative to the initial model


[Parallel(n_jobs=1)]: Done 600 out of 600 | elapsed:   43.7s finished


In [182]:
hm_non_linear_svm_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [183]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [184]:
scores

array([0.45      , 0.38333333, 0.475     , 0.45      ])

In [185]:
mean_score

0.4395833333333333

In [186]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [187]:
scores

array([0.43333333, 0.34166667, 0.29166667, 0.35833333])

In [188]:
mean_score

0.35625

In [189]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [190]:
scores

array([0.45      , 0.46666667, 0.31666667, 0.4       , 0.36666667,
       0.46666667, 0.56666667, 0.51666667])

In [191]:
mean_score

0.44375

In [192]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [193]:
scores

array([0.43333333, 0.35      , 0.33333333, 0.35      , 0.3       ,
       0.4       , 0.4       , 0.28333333])

In [194]:
mean_score

0.35625

In [195]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [196]:
hm_non_linear_svm_ros = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [197]:
hm_non_linear_svm_ros.fit()

Initial Model with Stock Params Score : 0.35625
Fitting 8 folds for each of 75 candidates, totalling 600 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5708333333333334
Improvement of 60.233918128654985% relative to the initial model


[Parallel(n_jobs=1)]: Done 600 out of 600 | elapsed:   44.0s finished


In [198]:
hm_non_linear_svm_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [199]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [200]:
scores

array([0.45      , 0.38333333, 0.475     , 0.45      ])

In [201]:
mean_score

0.4395833333333333

In [202]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [203]:
scores

array([0.43333333, 0.34166667, 0.29166667, 0.35833333])

In [204]:
mean_score

0.35625

In [205]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [206]:
scores

array([0.45      , 0.46666667, 0.31666667, 0.4       , 0.36666667,
       0.46666667, 0.56666667, 0.51666667])

In [207]:
mean_score

0.44375

In [208]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [209]:
scores

array([0.43333333, 0.35      , 0.33333333, 0.35      , 0.3       ,
       0.4       , 0.4       , 0.28333333])

In [210]:
mean_score

0.35625

In [211]:
# other metrics + graphs




### Hyper_optimized model

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [212]:
hm_non_linear_svm_to = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [213]:
hm_non_linear_svm_to.fit()

Initial Model with Stock Params Score : 0.4395833333333333
Fitting 4 folds for each of 75 candidates, totalling 300 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5541666666666667
Improvement of 26.066350710900483% relative to the initial model


[Parallel(n_jobs=1)]: Done 300 out of 300 | elapsed:   17.4s finished


In [214]:
hm_non_linear_svm_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [215]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [216]:
scores

array([0.55      , 0.4       , 0.50833333, 0.75833333])

In [217]:
mean_score

0.5541666666666667

In [218]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [219]:
scores

array([0.50833333, 0.53333333, 0.55833333, 0.525     ])

In [220]:
mean_score

0.53125

In [221]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [222]:
scores

array([0.66666667, 0.46666667, 0.38333333, 0.45      , 0.48333333,
       0.51666667, 0.61666667, 0.65      ])

In [223]:
mean_score

0.5291666666666667

In [224]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [225]:
scores

array([0.55      , 0.46666667, 0.5       , 0.55      , 0.55      ,
       0.56666667, 0.55      , 0.51666667])

In [226]:
mean_score

0.53125

In [227]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [228]:
hm_non_linear_svm_tos = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [229]:
hm_non_linear_svm_tos.fit()

Initial Model with Stock Params Score : 0.35625
Fitting 4 folds for each of 75 candidates, totalling 300 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.55
Improvement of 54.385964912280706% relative to the initial model


[Parallel(n_jobs=1)]: Done 300 out of 300 | elapsed:   17.6s finished


In [230]:
hm_non_linear_svm_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [231]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [232]:
scores

array([0.55833333, 0.36666667, 0.50833333, 0.23333333])

In [233]:
mean_score

0.4166666666666667

In [234]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [235]:
scores

array([0.51666667, 0.53333333, 0.61666667, 0.53333333])

In [236]:
mean_score

0.55

In [237]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [238]:
scores

array([0.63333333, 0.48333333, 0.35      , 0.38333333, 0.5       ,
       0.51666667, 0.8       , 0.73333333])

In [239]:
mean_score

0.55

In [240]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [241]:
scores

array([0.55      , 0.48333333, 0.5       , 0.56666667, 0.63333333,
       0.6       , 0.53333333, 0.53333333])

In [242]:
mean_score

0.55

In [243]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [244]:
hm_non_linear_svm_ro = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [245]:
hm_non_linear_svm_ro.fit()

Initial Model with Stock Params Score : 0.44375
Fitting 8 folds for each of 75 candidates, totalling 600 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.55
Improvement of 23.943661971831002% relative to the initial model


[Parallel(n_jobs=1)]: Done 600 out of 600 | elapsed:   43.6s finished


In [246]:
hm_non_linear_svm_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [247]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [248]:
scores

array([0.55833333, 0.36666667, 0.50833333, 0.23333333])

In [249]:
mean_score

0.4166666666666667

In [250]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [251]:
scores

array([0.51666667, 0.53333333, 0.61666667, 0.53333333])

In [252]:
mean_score

0.55

In [253]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [254]:
scores

array([0.63333333, 0.48333333, 0.35      , 0.38333333, 0.5       ,
       0.51666667, 0.8       , 0.73333333])

In [255]:
mean_score

0.55

In [256]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [257]:
scores

array([0.55      , 0.48333333, 0.5       , 0.56666667, 0.63333333,
       0.6       , 0.53333333, 0.53333333])

In [258]:
mean_score

0.55

In [259]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [260]:
hm_non_linear_svm_ros = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [261]:
hm_non_linear_svm_ros.fit()

Initial Model with Stock Params Score : 0.35625
Fitting 8 folds for each of 75 candidates, totalling 600 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5708333333333334
Improvement of 60.233918128654985% relative to the initial model


[Parallel(n_jobs=1)]: Done 600 out of 600 | elapsed:   44.1s finished


In [262]:
hm_non_linear_svm_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [263]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [264]:
scores

array([0.49166667, 0.54166667, 0.49166667, 0.51666667])

In [265]:
mean_score

0.5104166666666666

In [266]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [267]:
scores

array([0.54166667, 0.45833333, 0.58333333, 0.575     ])

In [268]:
mean_score

0.5395833333333333

In [269]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [270]:
scores

array([0.53333333, 0.5       , 0.53333333, 0.5       , 0.51666667,
       0.46666667, 0.45      , 0.48333333])

In [271]:
mean_score

0.4979166666666667

In [272]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [273]:
scores

array([0.65      , 0.55      , 0.46666667, 0.5       , 0.66666667,
       0.53333333, 0.65      , 0.55      ])

In [274]:
mean_score

0.5708333333333334

In [275]:
# other metrics + graphs




## Random Forest Classifier

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [276]:
hm_rf_to = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [277]:
hm_rf_to.fit()

Initial Model with Stock Params Score : 0.4375
Fitting 4 folds for each of 300 candidates, totalling 1200 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed: 122.2min finished


Random HP Search Best Model Score : 0.4833333333333333
Improvement of 10.476190476190464% relative to the initial model


In [278]:
hm_rf_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [279]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [280]:
scores

array([0.55      , 0.38333333, 0.475     , 0.39166667])

In [281]:
mean_score

0.44999999999999996

In [282]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [283]:
scores

array([0.45      , 0.4       , 0.39166667, 0.4       ])

In [284]:
mean_score

0.41041666666666665

In [285]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [286]:
scores

array([0.55      , 0.5       , 0.38333333, 0.48333333, 0.43333333,
       0.51666667, 0.58333333, 0.53333333])

In [287]:
mean_score

0.4979166666666667

In [288]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [289]:
scores

array([0.6       , 0.4       , 0.35      , 0.51666667, 0.53333333,
       0.35      , 0.41666667, 0.33333333])

In [290]:
mean_score

0.4375

In [291]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [292]:
hm_rf_tos = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [293]:
hm_rf_tos.fit()

Initial Model with Stock Params Score : 0.3875
Fitting 4 folds for each of 300 candidates, totalling 1200 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed: 140.0min finished


Random HP Search Best Model Score : 0.4375
Improvement of 12.90322580645161% relative to the initial model


In [294]:
hm_rf_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [295]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [296]:
scores

array([0.50833333, 0.39166667, 0.55      , 0.44166667])

In [297]:
mean_score

0.47291666666666665

In [298]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [299]:
scores

array([0.38333333, 0.425     , 0.45      , 0.41666667])

In [300]:
mean_score

0.41875

In [301]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [302]:
scores

array([0.51666667, 0.38333333, 0.38333333, 0.38333333, 0.53333333,
       0.55      , 0.63333333, 0.46666667])

In [303]:
mean_score

0.48125000000000007

In [304]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [305]:
scores

array([0.4       , 0.46666667, 0.31666667, 0.43333333, 0.4       ,
       0.48333333, 0.33333333, 0.4       ])

In [306]:
mean_score

0.4041666666666667

In [307]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [308]:
hm_rf_ro = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [309]:
hm_rf_ro.fit()

Initial Model with Stock Params Score : 0.4895833333333333
Fitting 8 folds for each of 300 candidates, totalling 2400 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed: 388.3min finished


Random HP Search Best Model Score : 0.5270833333333333
Improvement of 7.659574468085113% relative to the initial model


In [310]:
hm_rf_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [311]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [312]:
scores

array([0.54166667, 0.38333333, 0.49166667, 0.4       ])

In [313]:
mean_score

0.4541666666666667

In [314]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [315]:
scores

array([0.41666667, 0.475     , 0.325     , 0.38333333])

In [316]:
mean_score

0.39999999999999997

In [317]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [318]:
scores

array([0.53333333, 0.46666667, 0.4       , 0.38333333, 0.53333333,
       0.48333333, 0.5       , 0.53333333])

In [319]:
mean_score

0.47916666666666663

In [320]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [321]:
scores

array([0.48333333, 0.5       , 0.38333333, 0.45      , 0.46666667,
       0.3       , 0.41666667, 0.41666667])

In [322]:
mean_score

0.42708333333333337

In [323]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [324]:
hm_rf_ros = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [325]:
hm_rf_ros.fit()

Initial Model with Stock Params Score : 0.4166666666666667
Fitting 8 folds for each of 300 candidates, totalling 2400 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed: 255.0min finished


Random HP Search Best Model Score : 0.45000000000000007
Improvement of 8.00000000000001% relative to the initial model


In [326]:
hm_rf_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [327]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [328]:
scores

array([0.53333333, 0.4       , 0.43333333, 0.44166667])

In [329]:
mean_score

0.45208333333333334

In [330]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [331]:
scores

array([0.50833333, 0.35      , 0.33333333, 0.43333333])

In [332]:
mean_score

0.40625

In [333]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [334]:
scores

array([0.55      , 0.5       , 0.36666667, 0.45      , 0.5       ,
       0.5       , 0.55      , 0.38333333])

In [335]:
mean_score

0.475

In [336]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [337]:
scores

array([0.36666667, 0.41666667, 0.41666667, 0.4       , 0.43333333,
       0.36666667, 0.48333333, 0.35      ])

In [338]:
mean_score

0.4041666666666667

In [339]:
# other metrics + graphs




### Hyper_optimized Model

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [343]:
hm_rf_to = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [344]:
hm_rf_to.fit()

Initial Model with Stock Params Score : 0.4354166666666667
Fitting 4 folds for each of 2 candidates, totalling 8 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   8 out of   8 | elapsed:   20.3s finished


Random HP Search Best Model Score : 0.46458333333333335
Improvement of 6.6985645933014375% relative to the initial model


In [346]:
hm_rf_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [347]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [348]:
scores

array([0.525     , 0.36666667, 0.51666667, 0.39166667])

In [349]:
mean_score

0.44999999999999996

In [350]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [351]:
scores

array([0.46666667, 0.41666667, 0.35833333, 0.41666667])

In [352]:
mean_score

0.41458333333333336

In [353]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [354]:
scores

array([0.56666667, 0.5       , 0.36666667, 0.38333333, 0.48333333,
       0.51666667, 0.66666667, 0.56666667])

In [355]:
mean_score

0.50625

In [356]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [357]:
scores

array([0.43333333, 0.45      , 0.36666667, 0.45      , 0.41666667,
       0.4       , 0.43333333, 0.31666667])

In [358]:
mean_score

0.4083333333333333

In [359]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [360]:
hm_rf_tos = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [361]:
hm_rf_tos.fit()

Initial Model with Stock Params Score : 0.41875
Fitting 4 folds for each of 2 candidates, totalling 8 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   8 out of   8 | elapsed:   19.8s finished


Random HP Search Best Model Score : 0.4145833333333333
Improvement of -0.9950248756219002% relative to the initial model


In [362]:
hm_rf_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [363]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [364]:
scores

array([0.575     , 0.36666667, 0.51666667, 0.36666667])

In [365]:
mean_score

0.45625000000000004

In [366]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [367]:
scores

array([0.475     , 0.425     , 0.33333333, 0.425     ])

In [368]:
mean_score

0.4145833333333333

In [369]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [370]:
scores

array([0.6       , 0.45      , 0.35      , 0.43333333, 0.48333333,
       0.53333333, 0.63333333, 0.55      ])

In [371]:
mean_score

0.5041666666666667

In [372]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [373]:
scores

array([0.46666667, 0.51666667, 0.4       , 0.46666667, 0.36666667,
       0.41666667, 0.41666667, 0.31666667])

In [374]:
mean_score

0.42083333333333334

In [375]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [376]:
hm_rf_ro = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [377]:
hm_rf_ro.fit()

Initial Model with Stock Params Score : 0.475
Fitting 8 folds for each of 2 candidates, totalling 16 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  16 out of  16 | elapsed:  1.1min finished


Random HP Search Best Model Score : 0.5041666666666667
Improvement of 6.140350877192984% relative to the initial model


In [378]:
hm_rf_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [379]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [380]:
scores

array([0.575     , 0.36666667, 0.51666667, 0.40833333])

In [381]:
mean_score

0.4666666666666667

In [382]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [383]:
scores

array([0.49166667, 0.43333333, 0.34166667, 0.4       ])

In [384]:
mean_score

0.41666666666666663

In [385]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [386]:
scores

array([0.61666667, 0.45      , 0.36666667, 0.41666667, 0.51666667,
       0.51666667, 0.71666667, 0.53333333])

In [387]:
mean_score

0.5166666666666666

In [388]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [389]:
scores

array([0.48333333, 0.51666667, 0.4       , 0.5       , 0.41666667,
       0.4       , 0.4       , 0.31666667])

In [390]:
mean_score

0.42916666666666664

In [391]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [392]:
hm_rf_ros = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [393]:
hm_rf_ros.fit()

Initial Model with Stock Params Score : 0.4166666666666667
Fitting 8 folds for each of 2 candidates, totalling 16 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  16 out of  16 | elapsed:  1.1min finished


Random HP Search Best Model Score : 0.4291666666666667
Improvement of 3.0000000000000027% relative to the initial model


In [394]:
hm_rf_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [395]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [396]:
scores

array([0.53333333, 0.375     , 0.5       , 0.325     ])

In [397]:
mean_score

0.4333333333333333

In [398]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [399]:
scores

array([0.475     , 0.43333333, 0.30833333, 0.40833333])

In [400]:
mean_score

0.40625

In [401]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [402]:
scores

array([0.6       , 0.5       , 0.35      , 0.4       , 0.45      ,
       0.53333333, 0.68333333, 0.51666667])

In [403]:
mean_score

0.5041666666666667

In [404]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [405]:
scores

array([0.41666667, 0.51666667, 0.4       , 0.41666667, 0.43333333,
       0.4       , 0.41666667, 0.35      ])

In [406]:
mean_score

0.41875

In [407]:
# other metrics + graphs




## XGBoost Classifier

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [408]:
hm_xgb_to = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [409]:
hm_xgb_to.fit()

[07:58:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:58:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:58:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:58:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[07:58:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:58:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:58:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:58:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[07:58:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:58:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:58:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:58:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[07:58:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:58:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:58:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:58:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[08:04:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:04:40] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:04:40] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:04:40] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:04:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:04:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:04:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:04:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:04:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:04:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:04:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:04:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed:  6.6min finished


[08:04:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Random HP Search Best Model Score : 0.5166666666666666
Improvement of 8.29694323144103% relative to the initial model


In [410]:
hm_xgb_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [411]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[08:04:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:04:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:04:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:04:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [412]:
scores

array([0.5       , 0.41666667, 0.49166667, 0.5       ])

In [413]:
mean_score

0.47708333333333336

In [414]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:04:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [415]:
scores

array([0.40833333, 0.44166667, 0.28333333, 0.38333333])

In [416]:
mean_score

0.37916666666666665

In [417]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:05:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [418]:
scores

array([0.53333333, 0.38333333, 0.4       , 0.38333333, 0.5       ,
       0.46666667, 0.46666667, 0.56666667])

In [419]:
mean_score

0.4625

In [420]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:05:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [421]:
scores

array([0.35      , 0.43333333, 0.31666667, 0.38333333, 0.38333333,
       0.31666667, 0.36666667, 0.33333333])

In [422]:
mean_score

0.36041666666666666

In [423]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [424]:
hm_xgb_tos = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [425]:
hm_xgb_tos.fit()

[08:05:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:07] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:07] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[08:05:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:05:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:05:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:05:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[08:12:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:12:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:12:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:12:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:12:32] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:12:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:12:34] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:12:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:12:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:12:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:12:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:12:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed:  7.8min finished


[08:12:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Random HP Search Best Model Score : 0.4083333333333333
Improvement of 7.692307692307694% relative to the initial model


In [426]:
hm_xgb_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [427]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[08:12:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:12:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:12:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:12:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [428]:
scores

array([0.5       , 0.41666667, 0.49166667, 0.5       ])

In [429]:
mean_score

0.47708333333333336

In [430]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:12:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:12:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:12:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:12:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [431]:
scores

array([0.40833333, 0.44166667, 0.28333333, 0.38333333])

In [432]:
mean_score

0.37916666666666665

In [433]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:13:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [434]:
scores

array([0.53333333, 0.38333333, 0.4       , 0.38333333, 0.5       ,
       0.46666667, 0.46666667, 0.56666667])

In [435]:
mean_score

0.4625

In [436]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:13:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [437]:
scores

array([0.35      , 0.43333333, 0.31666667, 0.38333333, 0.38333333,
       0.31666667, 0.36666667, 0.33333333])

In [438]:
mean_score

0.36041666666666666

In [439]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [440]:
hm_xgb_ro = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [441]:
hm_xgb_ro.fit()

[08:13:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[08:13:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:09] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:13:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:17] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:17] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:13:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:13:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[08:46:14] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:46:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:46:19] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:46:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:47:27] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:47:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:47:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:47:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:48:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:48:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:48:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:48:27] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed: 35.9min finished


[08:49:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Random HP Search Best Model Score : 0.5375
Improvement of 16.216216216216207% relative to the initial model


In [442]:
hm_xgb_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [443]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[08:49:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:49:17] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:49:19] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:49:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [444]:
scores

array([0.5       , 0.41666667, 0.49166667, 0.5       ])

In [445]:
mean_score

0.47708333333333336

In [446]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:49:45] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:49:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:49:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:49:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [447]:
scores

array([0.40833333, 0.44166667, 0.28333333, 0.38333333])

In [448]:
mean_score

0.37916666666666665

In [449]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:50:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:50:19] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:50:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:50:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [450]:
scores

array([0.53333333, 0.38333333, 0.4       , 0.38333333, 0.5       ,
       0.46666667, 0.46666667, 0.56666667])

In [451]:
mean_score

0.4625

In [452]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[08:51:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:51:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:51:07] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:51:09] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [453]:
scores

array([0.35      , 0.43333333, 0.31666667, 0.38333333, 0.38333333,
       0.31666667, 0.36666667, 0.33333333])

In [454]:
mean_score

0.36041666666666666

In [455]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [456]:
hm_xgb_ros = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [457]:
hm_xgb_ros.fit()

[08:52:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:52:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:52:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:52:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[08:52:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:52:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:52:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:52:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:53:09] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:53:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:53:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:53:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[08:54:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:54:12] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:54:14] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:54:17] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[10:20:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:20:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:20:37] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:20:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[10:21:43] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:21:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:21:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:21:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[10:22:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:22:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:22:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:22:41] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed: 91.0min finished


[10:23:18] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Random HP Search Best Model Score : 0.4
Improvement of 10.982658959537579% relative to the initial model


In [458]:
hm_xgb_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [459]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[10:23:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:23:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:23:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:23:37] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [460]:
scores

array([0.5       , 0.41666667, 0.49166667, 0.5       ])

In [461]:
mean_score

0.47708333333333336

In [462]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[10:24:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:24:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:24:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:24:09] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [463]:
scores

array([0.40833333, 0.44166667, 0.28333333, 0.38333333])

In [464]:
mean_score

0.37916666666666665

In [465]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[10:24:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:24:34] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:24:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:24:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [466]:
scores

array([0.53333333, 0.38333333, 0.4       , 0.38333333, 0.5       ,
       0.46666667, 0.46666667, 0.56666667])

In [467]:
mean_score

0.4625

In [468]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[10:25:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:25:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:25:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:25:18] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [469]:
scores

array([0.35      , 0.43333333, 0.31666667, 0.38333333, 0.38333333,
       0.31666667, 0.36666667, 0.33333333])

In [470]:
mean_score

0.36041666666666666

In [471]:
# other metrics + graphs




### Hyper_optimized model

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [472]:
hm_xgb_to = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [473]:
hm_xgb_to.fit()

[10:26:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:26:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:26:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:26:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[10:26:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:26:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:26:23] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:26:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[10:27:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:27:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:27:17] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:27:19] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[10:28:29] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:28:30] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:28:34] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[10:28:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[11:12:09] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:12:10] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:12:12] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:12:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[11:12:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:12:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:12:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:13:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[11:13:48] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:13:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:13:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:13:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed: 47.9min finished


[11:14:10] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Random HP Search Best Model Score : 0.5166666666666666
Improvement of 8.29694323144103% relative to the initial model


In [474]:
hm_xgb_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [475]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[11:14:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:14:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:14:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:14:27] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [476]:
scores

array([0.63333333, 0.39166667, 0.55833333, 0.48333333])

In [477]:
mean_score

0.5166666666666666

In [478]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[11:14:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:14:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:14:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:14:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [479]:
scores

array([0.39166667, 0.39166667, 0.29166667, 0.36666667])

In [480]:
mean_score

0.36041666666666666

In [481]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[11:15:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:15:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:15:26] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:15:28] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [482]:
scores

array([0.53333333, 0.48333333, 0.38333333, 0.45      , 0.48333333,
       0.5       , 0.66666667, 0.53333333])

In [483]:
mean_score

0.5041666666666667

In [484]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[11:15:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:15:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:16:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:16:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [485]:
scores

array([0.31666667, 0.41666667, 0.28333333, 0.41666667, 0.35      ,
       0.3       , 0.33333333, 0.28333333])

In [486]:
mean_score

0.3375

In [487]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [488]:
hm_xgb_tos = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [489]:
hm_xgb_tos.fit()

[11:16:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:16:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:16:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:16:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[11:17:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:17:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:17:07] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:17:09] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[11:18:09] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:18:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:18:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:18:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[11:19:12] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:19:14] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:19:18] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:19:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[11:55:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:55:37] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:55:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:55:40] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[11:56:18] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:56:19] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:56:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:56:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[11:56:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:57:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:57:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:57:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed: 40.2min finished


[11:57:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Random HP Search Best Model Score : 0.4083333333333333
Improvement of 7.692307692307694% relative to the initial model


In [490]:
hm_xgb_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [491]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[11:57:27] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:57:29] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:57:30] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:57:32] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [492]:
scores

array([0.5       , 0.40833333, 0.53333333, 0.46666667])

In [493]:
mean_score

0.4770833333333333

In [494]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[11:57:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:57:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:58:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:58:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [495]:
scores

array([0.45      , 0.35833333, 0.41666667, 0.40833333])

In [496]:
mean_score

0.4083333333333333

In [497]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[11:58:27] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:58:28] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:58:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:58:32] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [498]:
scores

array([0.53333333, 0.38333333, 0.38333333, 0.45      , 0.48333333,
       0.51666667, 0.56666667, 0.6       ])

In [499]:
mean_score

0.4895833333333333

In [500]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[11:59:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:59:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:59:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[11:59:07] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [501]:
scores

array([0.33333333, 0.51666667, 0.35      , 0.38333333, 0.33333333,
       0.41666667, 0.3       , 0.38333333])

In [502]:
mean_score

0.3770833333333333

In [503]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [504]:
hm_xgb_ro = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [505]:
hm_xgb_ro.fit()

[11:59:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[12:00:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[12:00:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[12:00:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[12:00:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[12:00:18] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[12:00:19] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[12:00:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[12:01:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[12:01:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[12:01:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[12:01:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[12:02:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[12:02:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[12:02:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[12:02:10] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[13:30:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:30:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:30:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:30:18] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[13:31:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:31:28] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:31:32] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:31:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[13:32:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:32:18] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:32:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:32:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed: 93.1min finished


[13:33:19] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Random HP Search Best Model Score : 0.5375
Improvement of 16.216216216216207% relative to the initial model


In [506]:
hm_xgb_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [507]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[13:33:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:33:37] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:33:41] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:33:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [508]:
scores

array([0.54166667, 0.475     , 0.5       , 0.51666667])

In [509]:
mean_score

0.5083333333333333

In [510]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[13:34:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:34:08] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:34:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:34:19] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [511]:
scores

array([0.375     , 0.35833333, 0.33333333, 0.38333333])

In [512]:
mean_score

0.3625

In [513]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[13:34:43] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:34:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:34:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:34:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [514]:
scores

array([0.58333333, 0.45      , 0.41666667, 0.6       , 0.53333333,
       0.6       , 0.53333333, 0.58333333])

In [515]:
mean_score

0.5375

In [516]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[13:35:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:35:41] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:35:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[13:35:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [517]:
scores

array([0.36666667, 0.38333333, 0.28333333, 0.43333333, 0.36666667,
       0.33333333, 0.3       , 0.38333333])

In [518]:
mean_score

0.35625

In [519]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [523]:
hm_xgb_ros = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [524]:
hm_xgb_ros.fit()

[15:36:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:36:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:36:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:37:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[15:37:27] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:37:37] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:37:43] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:37:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done  16 out of  16 | elapsed:  1.5min finished


[15:38:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Random HP Search Best Model Score : 0.3958333333333333
Improvement of 9.826589595375719% relative to the initial model


In [525]:
hm_xgb_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [526]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[15:39:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:39:28] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:39:34] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:39:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [527]:
scores

array([0.48333333, 0.39166667, 0.46666667, 0.54166667])

In [528]:
mean_score

The history saving thread hit an unexpected error (OperationalError('database is locked')).History will not be written to the database.

0.4708333333333333

In [529]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[15:39:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:40:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:40:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:40:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [530]:
scores

array([0.46666667, 0.48333333, 0.40833333, 0.375     ])

In [531]:
mean_score

0.43333333333333335

In [532]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[15:40:31] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:40:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:40:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:40:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [533]:
scores

array([0.46666667, 0.4       , 0.43333333, 0.43333333, 0.41666667,
       0.45      , 0.46666667, 0.46666667])

In [534]:
mean_score

0.44166666666666665

In [535]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[15:41:30] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:41:40] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:41:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[15:41:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [536]:
scores

array([0.35      , 0.31666667, 0.31666667, 0.41666667, 0.45      ,
       0.55      , 0.36666667, 0.4       ])

In [537]:
mean_score

0.3958333333333333

In [538]:
# other metrics + graphs


